In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [7]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 29,]

In [8]:
head(dat)

Date       home.name away.name home.number away.number round period
154 2019-04-22 HW        GE        10           8          5     28    
155 2019-04-21 AD        GC         1           7          5     28    
156 2019-04-21 WB        CA        17           3          5     28    
157 2019-04-20 RI        SY        14          16          5     28    
158 2019-04-20 ME        SK        11          15          5     28    
159 2019-04-20 GW        FR         9           6          5     28    
    home.score away.score home.goals ... Total.Score.Max Total.Score.Close
154  90        113        13         ... 166.5           163.5            
155 119         46        18         ... 159.5           159.5            
156  57        101         7         ... 160.5           160.5            
157  89         67        13         ... 169.5           169.5            
158  55         95         7         ... 173.5           173.5            
159  82        106        11         ... 163.5           163.5            
    Total.Score.Over.Open Total.Score.Over.Min Total.Score.Over.Max
154 1.89                  1.89                 1.89                
155 1.89                  1.89                 1.91                
156 1.89                  1.89                 1.91                
157 1.89                  1.89                 1.91                
158 1.89                  1.89                 1.91                
159 1.89                  1.89                 1.91                
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
154 1.91                   1.89                   1.89                 
155 1.91                   1.89                   1.89                 
156 1.91                   1.89                   1.89                 
157 1.91                   1.89                   1.89                 
158 1.91                   1.89                   1.89                 
159 1.91                   1.89                   1.89                 
    Total.Score.Under.Max Total.Score.Under.Close
154 1.89                  1.91                   
155 1.91                  1.91                   
156 1.91                  1.91                   
157 1.91                  1.91                   
158 1.91                  1.91                   
159 1.91                  1.91

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [9]:
matchup <- data[data$period == 29,]
n.matches <- length(matchup$home.number)
matchup

Date       home.name away.name home.number away.number round period
145 2019-04-28 GE        WC         8          18          6     29    
146 2019-04-28 HW        CA        10           3          6     29    
147 2019-04-27 FR        WB         6          17          6     29    
148 2019-04-27 SY        GW        16           9          6     29    
149 2019-04-27 SK        AD        15           1          6     29    
150 2019-04-27 GC        BL         7           2          6     29    
151 2019-04-26 PA        NM        13          12          6     29    
152 2019-04-25 ES        CW         5           4          6     29    
153 2019-04-24 RI        ME        14          11          6     29    
    home.score away.score home.goals ... Total.Score.Max Total.Score.Close
145 104         46        15         ... 165.5           161.5            
146  93         88        13         ... 165.5           163.5            
147  88         69        13         ... 166.5           166.5            
148  79        120        12         ... 164.5           161.5            
149  68         97        10         ... 169.5           168.5            
150  62        111         9         ... 174.5           170.5            
151  88         72        12         ... 173.5           169.5            
152  69         73        10         ... 176.5           175.5            
153  85         42        12         ... 173.5           173.5            
    Total.Score.Over.Open Total.Score.Over.Min Total.Score.Over.Max
145 1.89                  1.89                 1.89                
146 1.89                  1.89                 1.91                
147 1.89                  1.89                 1.91                
148 1.89                  1.91                 1.89                
149 1.89                  1.89                 1.91                
150 1.89                  1.91                 1.89                
151 1.89                  1.91                 1.89                
152 1.89                  1.89                 1.91                
153 1.89                  1.89                 1.91                
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
145 1.91                   1.89                   1.89                 
146 1.91                   1.89                   1.89                 
147 1.91                   1.89                   1.89                 
148 1.91                   1.89                   1.91                 
149 1.91                   1.89                   1.89                 
150 1.91                   1.89                   1.91                 
151 1.91                   1.89                   1.91                 
152 1.91                   1.89                   1.89                 
153 1.91                   1.89                   1.89                 
    Total.Score.Under.Max Total.Score.Under.Close
145 1.89                  1.91                   
146 1.91                  1.91                   
147 1.91                  1.91                   
148 1.89                  1.91                   
149 1.91                  1.91                   
150 1.89                  1.91                   
151 1.89                  1.91                   
152 1.91                  1.91                   
153 1.91                  1.91

# Data

In [10]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [11]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [12]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [13]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [14]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [11]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd   2.5%    25%    50%    75%
delta                      0.65    0.00   0.07   0.51   0.61   0.66   0.70
attackGoals_raw[1,1]       1.91    0.10   2.54  -3.27   0.21   2.10   3.70
attackGoals_raw[1,2]      -4.70    0.11   2.77  -8.87  -6.93  -5.00  -2.70
attackGoals_raw[1,3]      -3.54    0.12   3.32  -8.79  -6.17  -3.85  -1.09
attackGoals_raw[1,4]      -0.07    0.12   3.10  -6.24  -2.22  -0.04   2.04
attackGoals_raw[1,5]       0.51    0.11   2.64  -4.56  -1.24   0.44   2.21
attackGoals_raw[1,6]       1.01    0.10   2.79  -4.61  -0.93   1.11   2.93
attackGoals_raw[1,7]      -0.10    0.10   2.57  -5.12  -1.84  -0.10   1.54
attackGoals_raw[1,8]       1.38    0.13   2.66  -3.90  -0.50   1.42   3.27
attackGoals_raw[1,9]       1.37    0.06   1.92  -2.32   0.09   1

In [15]:
fit <- sflist2stanfit(sflist)

In [16]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     6.439207e-01 0.0010688015   0.06676127  5.095378e-01
attackGoals_raw[1,1]      1.766318e+00 0.0502453316   2.71141531 -3.395418e+00
attackGoals_raw[1,2]     -4.778208e+00 0.0517452016   2.85898031 -8.963320e+00
attackGoals_raw[1,3]     -3.525135e+00 0.0581013225   3.35671726 -8.792436e+00
attackGoals_raw[1,4]     -2.466451e-01 0.0633689348   3.12523347 -6.302248e+00
attackGoals_raw[1,5]      5.199669e-01 0.0527714940   2.73845655 -4.812840e+00
attackGoals_raw[1,6]      9.182184e-01 0.0549345941   2.91719552 -4.921439e+00
attackGoals_raw[1,7]     -1.998410e-01 0.0528051029   2.58211200 -5.326134e+00
attackGoals_raw[1,8]      1.361928e+00 0.0546075097   2.79770670 -4.078263e+00
attackGoals_raw[1,9]      1.313544e+00 0.0339462711   1.92024878 -2.449518e+00
attackGoals_raw[1,10]     1.594662e+00 0.0424918172   2.25747137 -2.860389e+00
attackGoals_raw[1,11]    -4.525866e-01 0.05

# Extract parameters

In [17]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [18]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [19]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [20]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [21]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [22]:
actual.total.diff
correct.vec

[1]  58   5  19 -41 -29 -49  16  -4  43

[1]  TRUE FALSE  TRUE  TRUE FALSE  TRUE  TRUE FALSE  TRUE

# Calculate percentage of win, loss and draw

In [23]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [24]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9]  
      [1,] 0.9712 0.2540 0.9768 0.3396 0.5648 0.4856 0.9574 0.5432 0.9572
      [2,] 0.0088 0.0264 0.0054 0.0394 0.0304 0.0690 0.0096 0.0504 0.0084
      [3,] 0.0200 0.7196 0.0178 0.6210 0.4048 0.4454 0.0330 0.4064 0.0344

In [25]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [26]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [28]:
sim.pred.mat

[,1]                [,2]     [,3]     [,4]    [,5]    [,6]   [,7]   
 [1,] behind diff         2.4574   2.305    3.9408  -4.48   1.913  1.1818 
 [2,] goal diff           19.1744  -4.2592  15.2312 -0.0044 1.2862 -0.2268
 [3,] total diff          117.5038 -23.2502 95.328  -4.5064 9.6302 -0.179 
 [4,] home team           GE       HW       FR      SY      SK     GC     
 [5,] away team           WC       CA       WB      GW      AD     BL     
 [6,] actual result       58       5        19      -41     -29    -49    
 [7,] prediction correct? TRUE     FALSE    TRUE    TRUE    FALSE  TRUE   
 [8,] home win prob       0.9712   0.254    0.9768  0.3396  0.5648 0.4856 
 [9,] draw prob           0.0088   0.0264   0.0054  0.0394  0.0304 0.069  
[10,] home loss prob      0.02     0.7196   0.0178  0.621   0.4048 0.4454 
[11,] simulated sd ests   152.6    48.88    121.74  21.44   56.53  25.25  
      [,8]    [,9]    [,10]  
 [1,] 13.6746 -0.5586 10.5736
 [2,] 5.2942  1.7156  7.452  
 [3,] 45.4398 9.735   55.2856
 [4,] PA      ES      RI     
 [5,] NM      CW      ME     
 [6,] 16      -4      43     
 [7,] TRUE    FALSE   TRUE   
 [8,] 0.9574  0.5432  0.9572 
 [9,] 0.0096  0.0504  0.0084 
[10,] 0.033   0.4064  0.0344 
[11,] 53.35   53.73   68.25